In [ ]:
import matplotlib.pyplot as plt


from defs import load_yaml
import numpy as np
from pathlib import Path
from swmmio.defs import INP_OBJECTS, INFILTRATION_COLS, RPT_OBJECTS, COMPOSITE_OBJECTS
from swmmio import Model

model_name = "HY006"
run_folder = Path(rf"C:\Users\everett\Documents\GitHub\camus_to\data\models\swmm\{model_name}\runs")
model_file = run_folder.parent / f"{model_name}.inp"
mdl = Model(str(model_file), crs="EPSG:26917")
node_args = {type:{} for type in COMPOSITE_OBJECTS['nodes']["inp_sections"]}
link_args = COMPOSITE_OBJECTS['links']["inp_sections"]

def _get_node_types(mdl) -> dict[str:str]:
    node_types = {}
    for sec in COMPOSITE_OBJECTS['nodes']["inp_sections"]:
        node_types.update({x:sec for x in getattr(mdl.inp, sec.lower()).index.tolist()})
    return node_types

def _get_link_types(mdl) -> dict[str:str]:
    link_types = {}
    for sec in COMPOSITE_OBJECTS['links']["inp_sections"]:
        link_types.update({x:sec for x in getattr(mdl.inp, sec.lower()).index.tolist()})
    return link_types


plotting_dict = load_yaml(Path("defs") / 'default_plot_args.yml')

node_types = _get_node_types(mdl)
link_types = _get_link_types(mdl)



m = mdl.subcatchments.geodataframe.explore(
    label="subcatchments",
    **plotting_dict["subcatchments"]
)

for node_type in COMPOSITE_OBJECTS['nodes']["inp_sections"]:
    idx = [x.lower() == node_type.lower() for x in list(node_types.values())]
    if np.any(idx):
        mdl.nodes.geodataframe.loc[idx].explore(
            m=m,
            label=node_type.lower(),
            **plotting_dict["nodes"][node_type.lower()]
        )

for link_type in COMPOSITE_OBJECTS['links']["inp_sections"]:
    idx = [x.lower() == link_type.lower() for x in list(link_types.values())]
    if np.any(idx):
        mdl.links.geodataframe.loc[idx].explore(
            m=m,
            label=link_type.lower(),
            **plotting_dict["links"][link_type.lower()]
        )


#mdl.subcatchments.geodataframe.explore(ax=ax, column="PercImperv")

c:\Users\everett\Documents\GitHub\optswmm\.venv\Lib\site-packages\swmmio\utils\dataframes.py:135: UserWarning: STORAGE section not found in C:\Users\everett\Documents\GitHub\camus_to\data\models\swmm\HY006\HY006.inp
  warnings.warn(f'{sect} section not found in {inp_path}')
c:\Users\everett\Documents\GitHub\optswmm\.venv\Lib\site-packages\swmmio\utils\dataframes.py:135: UserWarning: WEIRS section not found in C:\Users\everett\Documents\GitHub\camus_to\data\models\swmm\HY006\HY006.inp
  warnings.warn(f'{sect} section not found in {inp_path}')
c:\Users\everett\Documents\GitHub\optswmm\.venv\Lib\site-packages\swmmio\utils\dataframes.py:135: UserWarning: ORIFICES section not found in C:\Users\everett\Documents\GitHub\camus_to\data\models\swmm\HY006\HY006.inp
  warnings.warn(f'{sect} section not found in {inp_path}')
c:\Users\everett\Documents\GitHub\optswmm\.venv\Lib\site-packages\swmmio\utils\dataframes.py:135: UserWarning: PUMPS section not found in C:\Users\everett\Documents\GitHub\camu

In [28]:
import contextily as ctx
import random
import folium
import matplotlib.cm as cm
import matplotlib.colors as mcolors



model_dir = Path(r"C:\Users\everett\Documents\GitHub\camus_to\data\models\swmm")
subdirs = [f for f in model_dir.iterdir() if f.is_dir()]

norm = mcolors.Normalize(vmin=0, vmax=len(subdirs))
cmap = cm.get_cmap('rainbow', len(subdirs))
nodes = {}
links = {}
subcatchments = {}

for ii, subdir in enumerate(subdirs):
    mdl = Model(str(subdir / f"{subdir.name}.inp"), crs="epsg:26917")
    subcatchments[subdir.stem] = mdl.subcatchments.geodataframe.copy()
    nodes[subdir.stem] = mdl.nodes.geodataframe.copy()
    links[subdir.stem] = mdl.links.geodataframe.copy()


ind = np.argsort([-c.area.sum() for c in subcatchments.values()])
subcatchments = {k: subcatchments[k] for k in np.array(list(subcatchments.keys()))[ind]}
nodes = {k: nodes[k] for k in np.array(list(nodes.keys()))[ind]}
links = {k: links[k] for k in np.array(list(links.keys()))[ind]}


subcatchments["HY104"] = subcatchments["HY104"].drop("s104", axis=0)


# Create a folium map object centered at an approximate location with finer zoom increments
m = folium.Map(location=[43.65107, -79.347015], zoom_start=9, tiles="cartodbpositron", zoom_control=True, control_scale=True, )
# Add a scale bar to the map
for ii, (k, v) in enumerate(subcatchments.items()):
    v.explore(m=m, label=k, alpha=1, fill=False, stroke=True, zorder=9, color="black")
    nodes[k].explore(m=m, color="black", label=k, markersize=5, alpha=1)
    outfalls = nodes[k][["HY" in n for n in nodes[k].index.to_list()]]
    links[k].explore(m=m, color="blue", label=k, alpha=1, linewidth=0.5)
    outfalls.explore(m=m, color="red", markersize=10, zorder=10)
m

C:\Users\everett\AppData\Local\Temp\ipykernel_43504\3542505069.py:13: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  cmap = cm.get_cmap('rainbow', len(subdirs))
c:\Users\everett\Documents\GitHub\optswmm\.venv\Lib\site-packages\swmmio\utils\dataframes.py:135: UserWarning: VERTICES section not found in C:\Users\everett\Documents\GitHub\camus_to\data\models\swmm\HY005\HY005.inp
  warnings.warn(f'{sect} section not found in {inp_path}')
c:\Users\everett\Documents\GitHub\optswmm\.venv\Lib\site-packages\swmmio\utils\dataframes.py:135: UserWarning: VERTICES section not found in C:\Users\everett\Documents\GitHub\camus_to\data\models\swmm\HY006\HY006.inp
  warnings.warn(f'{sect} section not found in {inp_path}')
c:\Users\everett\Documents\GitHub\optswmm\.venv\Lib\site-packages\swmmio\utils\dataframes.py:135: UserWarning: